(ch_GEEsampleRegions)=
# Extracting data
Now that we know (a) how to load ``ee.Image()``s and filter ``ee.ImageCollection()``s, (b) create and download ``ee.FeatureCollection()``s, what we want to look at in this short section is: how to bring the things together. Specifically, we show here how to get the values of a single image. After that we apply this to the functions we have described before to download the data. We take as an example again our two points stored in ``fc`` and the ``GFW`` data.

In [33]:
import ee
import geemap
try:
    ee.Initialize()
except Exception as e:
    ee.Authenticate()
    ee.Initialize()

In [34]:
point_geom = ee.Geometry.Point([-60, -20])
point_feat = ee.Feature(point_geom, {'ID': 1})
point_geom_2 = ee.Geometry.Point([-61, -21])
point_feat_2 = ee.Feature(point_geom_2, {'ID': 2})
fc = ee.FeatureCollection([point_feat, point_feat_2])

In [3]:
fc

In [30]:
gfw = ee.Image("UMD/hansen/global_forest_change_2023_v1_11").select(['treecover2000'])
gfw

The code needed for this is pretty straight forward:

In [31]:
vals = gfw.sampleRegions(collection=fc, properties=['ID'], scale=30, tileScale=16, geometries=False)

You can have a more detailed look into the [documentation](https://developers.google.com/earth-engine/apidocs/ee-image-sampleregions#:~:text=Converts%20each%20pixel%20of%20an%20image%20%28at%20a,any%20specified%20properties%20copied%20from%20the%20input%20feature.), but here is already a brief description of the function:
* ``gfw.sampleRegions()``: this basically means, that we take the image (all bands) and take a sample from it (aka: different smaller *regions*)
* ``collection``: are the features that we want to get the values for
* ``properties``: a list of attributes from the original feature collection that you want to keep
* ``scale``: is the spatial resolution in ``meters`` at which the values should be extracted. Since we know that the GFW data are from Landsat, we use 30m as a spatial resolution. If we were to use e.g., Sentinel-2 data, we would modify this to 10
* ``tileScale``: this is a factor for Earth Engine on how to subdivide the points. The more points and the larger the overall coverage is, the larger you want to choose the value
* ``geometries``: whether or not the geometries should be loaded to the client as well. With many points or complex geometries this increases the data size substantially.

Using our data coverters from the [previous chapter](ch_GEEconverters) we can now convert the data into a pandas dataframe and are done :-)

In [32]:
df = ee.data.computeFeatures({
    'expression': vals,
    'fileFormat': 'PANDAS_DATAFRAME'})
df

geo  ID  treecover2000
0  None   1             53
1  None   2              0